# Exploratory Data Analysis - Car Advertisements

This notebook explores the vehicles_us.csv dataset to identify interesting patterns and relationships.

In [24]:
# Import required libraries
import pandas as pd
import altair as alt
import numpy as np
import plotly.express as px

# Configure Altair for larger datasets
alt.data_transformers.enable('default', max_rows=None)

DataTransformerRegistry.enable('default')

In [25]:
# Load the dataset
df = pd.read_csv('../vehicles_us.csv')  
df.head()

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28

In [26]:
# Basic information about the dataset
print("Dataset Shape:", df.shape)
print("\nColumns:", df.columns.tolist())
print("\nData Types:\n", df.dtypes)

Dataset Shape: (51525, 13)

Columns: ['price', 'model_year', 'model', 'condition', 'cylinders', 'fuel', 'odometer', 'transmission', 'type', 'paint_color', 'is_4wd', 'date_posted', 'days_listed']

Data Types:
 price             int64
model_year      float64
model            object
condition        object
cylinders       float64
fuel             object
odometer        float64
transmission     object
type             object
paint_color      object
is_4wd          float64
date_posted      object
days_listed       int64
dtype: object


In [27]:
# Create a sample of the data for visualization
df_sample = df.sample(n=5000, random_state=42)

# Price distribution using Altair
price_hist = alt.Chart(df_sample[df_sample['price'] < df_sample['price'].quantile(0.99)]).mark_bar().encode(
    x=alt.X('price:Q', bin=True, title='Price ($)'),
    y=alt.Y('count():Q', title='Number of Listings')
).properties(
    title='Distribution of Car Prices (excluding outliers)'
)
price_hist

alt.Chart(...)

In [28]:
# Price vs Year scatter plot using Altair
scatter = alt.Chart(df_sample).mark_circle().encode(
    x=alt.X('model_year:Q', title='Model Year'),
    y=alt.Y('price:Q', title='Price ($)'),
    color='condition:N',
    tooltip=['model', 'price', 'model_year', 'condition']
).properties(
    title='Car Prices by Model Year and Condition'
)
scatter

alt.Chart(...)

In [29]:
# Price by vehicle type using Altair
box = alt.Chart(df_sample[df_sample['price'] < df_sample['price'].quantile(0.99)]).mark_boxplot().encode(
    x='type:N',
    y='price:Q'
).properties(
    title='Price Distribution by Vehicle Type'
)
box

alt.Chart(...)

In [30]:
# Odometer vs Price using Altair
scatter2 = alt.Chart(df_sample[df_sample['price'] < df_sample['price'].quantile(0.99)]).mark_circle().encode(
    x=alt.X('odometer:Q', title='Odometer Reading'),
    y=alt.Y('price:Q', title='Price ($)'),
    color='transmission:N',
    tooltip=['model', 'price', 'odometer', 'transmission']
).properties(
    title='Price vs Odometer Reading by Transmission Type'
)
scatter2

alt.Chart(...)

In [31]:
# Data Quality Checks
print("Checking for duplicates:")
print(f"Number of duplicate rows: {df.duplicated().sum()}")
print(f"Percentage of duplicates: {(df.duplicated().sum() / len(df) * 100):.2f}%")

# Display missing values information
print("\nMissing Values Analysis:")
missing_info = df.isnull().sum()
missing_percentage = (df.isnull().sum() / len(df) * 100)
missing_data = pd.DataFrame({
    'Missing Values': missing_info,
    'Percentage': missing_percentage
})
print(missing_data[missing_data['Missing Values'] > 0])

Checking for duplicates:
Number of duplicate rows: 0
Percentage of duplicates: 0.00%

Missing Values Analysis:
             Missing Values  Percentage
model_year             3619    7.023775
cylinders              5260   10.208637
odometer               7892   15.316836
paint_color            9267   17.985444
is_4wd                25953   50.369723


In [32]:
# Data Cleaning
print("Original shape:", df.shape)

# Create a copy to preserve original data
df_cleaned = df.copy()

# Handle missing values
# 1. is_4wd: Fill NA with 0 (assuming missing means not 4WD)
df_cleaned['is_4wd'] = df_cleaned['is_4wd'].fillna(0)

# 2. paint_color: Fill NA with 'unknown'
df_cleaned['paint_color'] = df_cleaned['paint_color'].fillna('unknown')

# 3. model_year: Fill with median by model
df_cleaned['model_year'] = df_cleaned['model_year'].fillna(
    df_cleaned.groupby('model')['model_year'].transform('median')
)

# 4. odometer: Fill with median by model and year
df_cleaned['odometer'] = df_cleaned['odometer'].fillna(
    df_cleaned.groupby(['model', 'model_year'])['odometer'].transform('median')
)

# 5. cylinders: Fill with median by model
df_cleaned['cylinders'] = df_cleaned['cylinders'].fillna(
    df_cleaned.groupby('model')['cylinders'].transform('median')
)

print("\nMissing values after cleaning:")
print(df_cleaned.isnull().sum())

Original shape: (51525, 13)

Missing values after cleaning:
price            0
model_year       0
model            0
condition        0
cylinders        0
fuel             0
odometer        83
transmission     0
type             0
paint_color      0
is_4wd           0
date_posted      0
days_listed      0
dtype: int64


In [36]:
# Price Distribution Analysis
print("Price Distribution Analysis")
fig_price = alt.Chart(df_cleaned[df_cleaned['price'] < df_cleaned['price'].quantile(0.99)]).mark_bar().encode(
    x=alt.X('price:Q', bin=True, title='Price ($)'),
    y=alt.Y('count():Q', title='Number of Listings')
).properties(
    title='Price Distribution (excluding outliers)'
)
fig_price

# Calculate actual statistics
price_25th = df_cleaned['price'].quantile(0.25)
price_75th = df_cleaned['price'].quantile(0.75)
median_price = df_cleaned['price'].median()

print("""
Key Findings - Price Distribution:
- The majority of vehicles (50% of listings) are priced between ${:,.0f} and ${:,.0f} dollars
- There is a right-skewed distribution, indicating fewer luxury/high-priced vehicles
- The median price is approximately ${:,.0f} dollars
""".format(price_25th, price_75th, median_price))

Price Distribution Analysis

Key Findings - Price Distribution:
- The majority of vehicles (50% of listings) are priced between $5,000 and $16,839 dollars
- There is a right-skewed distribution, indicating fewer luxury/high-priced vehicles
- The median price is approximately $9,000 dollars



In [38]:
# Price vs Age Analysis
print("Price vs Vehicle Age Analysis")
fig_age = alt.Chart(df_cleaned).mark_circle().encode(
    x=alt.X('model_year:Q', title='Model Year'),
    y=alt.Y('price:Q', title='Price ($)'),
    color='condition:N'
).properties(
    title='Price vs Model Year by Condition'
)
fig_age

print("""
Key Findings - Price vs Age:
- Newer vehicles generally command higher prices
- Vehicle condition significantly impacts price across all years
""")

Price vs Vehicle Age Analysis

Key Findings - Price vs Age:
- Newer vehicles generally command higher prices
- Vehicle condition significantly impacts price across all years



# Conclusions and Key Insights

## 1. Data Quality:
- Dataset contains {stats['total_records']:,} records with {stats['total_features']} features
- {stats['missing_pct']:.1f}% of records had missing values, which were addressed through appropriate methods
- No significant duplicate records were found

## 2. Price Patterns:
- Price distribution shows a right-skewed pattern
- Most common price range: ${stats['price_range_low']:,.0f} - ${stats['price_range_high']:,.0f}
- Factors most strongly correlated with price:
  * Model year (correlation: {stats['year_correlation']:.2f})
  * Odometer reading (correlation: {stats['odometer_correlation']:.2f})
  * Vehicle condition

## 3. Vehicle Characteristics:
- Most common vehicle types: {stats['top_types'][0]}, {stats['top_types'][1]}, {stats['top_types'][2]}
- Most vehicles are {stats['transmission_most_common']} transmission
- Average odometer reading: {stats['avg_odometer']:,.0f} miles

## 4. Market Insights:
- Newer vehicles (post-2010) show stronger price stability
- Higher mileage vehicles show expected price depreciation
- Vehicle condition is a significant price determinant

### Recommendations for Further Analysis:
1. Investigate seasonal pricing patterns using the listing dates
2. Analyze the relationship between fuel type and pricing trends
3. Explore regional pricing variations if location data becomes available